# Lab: Basic Premium Metrics

In this lab, we take a closer look at how the premium metrics we've discussed so far behave. The lab is based on a synthetic policy dataset we constructed to be as simple as possible while exhibiting the typical behaviors we want to highlight.

The core of the lab is to answer questions about the data and its behavior. Sometimes, we'll be plotting behaviors of the data set. Typically, there will be questions both before and after each plot. **Try to answer the pre-plot questions before showing the plot!** The point of these question is to encourage you to think about what you expect to see before you see it. The post-plot questions are designed to call your attention to specific features of the plot you may not have expected or noticed.

In [ ]:
import datetime
import calendar

import pandas as pd

import plotly.express as px
import plotly.io as pio

from policy_metrics import *

In [ ]:
pio.renderers.default = "png"

## The Data

Below, we read in the data set for the lab. The data set for the lab is a set of made-up policy data that conforms to the simple schema laid out in the previous section. A few rows from the data set are shown below, but you are encouraged to download the complete data set from [here](data/lab-1-policy.csv).

In [ ]:
policy_df = pd.read_csv(
    "data/lab-1-policy.csv",
    parse_dates=["policy_effective_date", "policy_expiration_date", "transaction_effective_date", "record_date"]
)
policy_df.head()

## Policy Data Questions

If it helps in answering these questions, feel free to explore the data set with Pandas, open the source CSV in Excel, or any other way that you're comfortable poking around with data.

1. How many distinct policies are in the data set?
1. How many years does the data set cover?
1. Examine the relationship between policy numbers, policy effective dates, and transaction type codes. How do the policy numbers appear to be constructed?
1. This is a workers' compensation program, and the unit of exposure is payroll. Does the relative magnitude of written exposure to written premium appear to be plausible?
1. What seems to be happening to written premium over time?

In [ ]:
evaluation_dates = [
    datetime.date(year, month, calendar.monthrange(year, month)[1])
    for year in range(2021, 2027)
    for month in range(1, 13)
]
experience_quarters = [
    (datetime.date(year, month, 1), datetime.date(year, month+2, calendar.monthrange(year, month+2)[1]))
    for year in range(2021, 2027)
    for month in [1, 4, 7, 10]
]

## Policy Metrics and Evaluation Dates

One of the more confusing aspects of insurance data is that there are two separate temporal dimensions: the point in time (for stocks) or period (for flows) you wish to measure, and the evaluation date -- the point in time at which you make the measurement. Both of these aspects can have very large impacts on the value of the metric.

This implies that there are at least two useful ways to exmaine the behavior of a metric. We can hold the experience period fixed and vary the evaluation date, or we can hold the evaluation date fixed and vary the experience period. We'll do both of these in this lab, but we'll start by varying the experience period.

In [ ]:
eval_date_metrics_2021 = pd.concat([
    policy_basis_metrics(policy_df, [(datetime.date(2021, 1, 1), datetime.date(2021, 12, 31))], evaluation_dates[:24]),
    accident_basis_metrics(policy_df, [(datetime.date(2021, 1, 1), datetime.date(2021, 12, 31))], evaluation_dates[:24]),
])
eval_date_metrics_2022 = pd.concat([
    policy_basis_metrics(policy_df, [(datetime.date(2022, 1, 1), datetime.date(2022, 12, 31))], evaluation_dates[12:36]),
    accident_basis_metrics(policy_df, [(datetime.date(2022, 1, 1), datetime.date(2022, 12, 31))], evaluation_dates[12:36]),
])

The plot below will show policy basis written premium, policy basis earned premium, and accident basis earned premium for policy year 2021 (`2021-01-01/2021-12-31`), as of every month-end evaluation date between January 2021 and December 2022. Before you generate the plot, think about the following questions:

1. What do you expect the ultimate value of policy basis written premium to be?
1. What do you expect the ultimate value of policy basis earned premium to be?
1. What do you expect the ultimate value of accident basis earned premium to be? Will it be the same ultimate value as policy basis earned premium?
1. Which of the metrics (if any) will reach its ultimate value first?

Now that you've thought about these questions, click the "Click to Show" button near the right-hand margin of the page.

In [ ]:
fig = px.line(
    eval_date_metrics_2021,
    x="Evaluation Date",
    y=["Written Premium", "Earned Premium"],
    facet_col="Risk Basis",
    template="plotly_white",
)
fig.show()

Now that you've seen the plot, consider the following questions:

1. Why does accident-basis earned premium stop changing after evaluation date `2021-12-31`? Will this always be true?
1. Why does policy-basis written premium stop changing after evaulation date `2021-12-31`? Will this always be true?
1. When is the difference between policy-basis earned and written premium greatest in absolute terms? In relative terms?
1. Why is policy-basis and accident-basis earned premium identical for evaluation dates in 2021? Will policy-basis and accident-basis earned premium always be the same?
1. What sort of mathematical function governs the shape of the earned premium curve? Why?

## Policy Metrics and Experience Periods

Now that we've seen how policy metrics vary as a function of evaluation date, let's see how they vary as a function of experience period. In the plot below, we'll show policy-basis and accident-basis earned premium by experience quarter, and we'll show every experience quarter from 2021Q1 to 2026Q4. All of the metrics will be shown as of evaluation date `2027-12-31`.

Before rendering the plot, consider the following questions:

1. What do you expect policy quarter earned premiums to be in 2021?
1. Between policy-basis and accident-basis earned premiums, do you expect one to be smoother and one to be more prone to jumps? If so, which one and why?
1. Why aren't we including policy quarter written premiums in this plot?

Now that you've thought about these questions, click the "Click to Show" button near the right-hand margin of the page.

In [ ]:
quarter_metrics = pd.concat([
    policy_basis_metrics(policy_df, experience_quarters, [datetime.date(2027, 12, 31)]),
    accident_basis_metrics(policy_df, experience_quarters, [datetime.date(2027, 12, 31)]),
])

fig = px.line(
    quarter_metrics,
    x="Period End",
    y="Earned Premium",
    color="Risk Basis",
    template="plotly_white",
)
fig.show()

Now that you've seen the plot, consider the following additional questions:

1. Why does the policy-basis earned premium show a stair-step pattern? Why doesn't the accident-basis earned premium show that pattern?
1. Note that accident-basis earned premium very slightly exceeds policy-basis earned premium in 2024Q3 and 2024Q4. Why?
1. If we sum up policy-basis earned premium for all quarters and compare it to the sum of accident-basis earned premium for all quarter, which will be larger? Why?
1. When would you want to use policy-basis earned premium? When would you want to use accident-basis earned premium? Why?

## Policy Metrics by Experience Period for an Accident Year

In the previous plot, we looked at quarterly premium metrics for an entire program over a five-year span. Now, we'll look at quarterly premium metrics for a single treaty year, which we'll assume covers `2021-01-01/2021-12-31`. All of the metrics will be evaluated as of `2023-03-31`. Before looking at the plot, consider the following questions:

1. Why are we doing this? What application does this have at Ledger?
1. What do you expect to see?

Now that you've thought about these questions, click the "Click to Show" button near the right-hand margin of the page.

In [ ]:
quarter_metrics_2022 = pd.concat([
    policy_basis_metrics(policy_df.iloc[:12, :], experience_quarters, [datetime.date(2023, 3, 31)]),
    accident_basis_metrics(policy_df.iloc[:12, :], experience_quarters, [datetime.date(2023, 3, 31)]),
])

fig = px.line(
    quarter_metrics_2022,
    x="Period End",
    y="Earned Premium",
    color="Risk Basis",
    template="plotly_white",
)
fig.show()

Now that you've seen the plot, consider the following questions:

1. What does this imply about how we should forecast transactions?
1. Why isn't earned premium in 2021Q4 and 2022Q1 identical?
1. Why isn't the earned premium triangle perfectly symmetrical?
1. What is the relationship between the metrics in this plot and the metrics in the first plot in this lab?
